# Feature Selection using the Adjusted Mutual Information (AMI) Score 

### (DNS analysis only)

This notebook uses the Adjusted Mutual Information Score to determine the most relevant features in the DDoS attacks. It uses the bigflows pcap from [http://tcpreplay.appneta.com/wiki/captures.html] containing normal network traffic. The DDoS attack pcaps from DDoSDB [https://ddosdb.org/] are used to compare it with the normal network traffic.

In [3]:
import Utils
print(Utils.uint32_to_ip(720657085))

189.90.244.42


In [3]:
#all relevant libraries need to be imported
from sklearn.metrics.cluster import adjusted_mutual_info_score, mutual_info_score, normalized_mutual_info_score
from sklearn.feature_selection import mutual_info_classif
import numpy as np
import dpkt
import Utils
import ipaddress
import pandas as pd
import time
import os
import csv
import json
import operator
import sys
# import dnslib
# from dns_packet import *
# from kaitaistruct import KaitaiStream, BytesIO
from scapy.all import *
from scapy.layers.dns import DNS, DNSQR
import logging
logging.getLogger("scapy.runtime").setLevel(logging.ERROR)

### Load bigflows containing only UDP traffic

In [4]:
start = time.time()

input = open('normal_pcaps/bigflows_dns.pcap', 'rb')
normal = dpkt.pcap.Reader(input)
length = 4372 #this is the number of packets in bigflows_udp.pcap   #791615 #791179

ips_n = np.full(length,-1)
protocol_n = np.full(length,-1)
total_length_n = np.full(length,-1)
src_port_n = np.full(length,-1)
dst_port_n = np.full(length,-1)
udp_length_n = np.full(length,-1)

dns_opcode_n = np.full(length,-1)
dns_answerlength_n = np.full(length,-1)
dns_questionlength_n = np.full(length,-1)
# dns_additional_recordlength_n = np.empty(length)
# dns_RRlength_n = np.empty(length)

dns_flag_response_n = np.full(length,-1)
dns_flag_truncated_n = np.full(length,-1)
dns_flag_authorative_n = np.full(length,-1)
dns_flag_recursiond_n = np.full(length,-1)
dns_flag_recursiona_n = np.full(length,-1)

dns_reply_code_n = np.full(length,-1)

dns_answer_type_n = np.full(length,-1)
dns_answer_class_n = np.full(length,-1)
dns_answer_name_n = np.full(length,-1)
dns_answer_size_n = np.full(length,-1)

dns_question_name_n = np.full(length,-1)
dns_question_class_n = np.full(length,-1)
dns_question_type_n = np.full(length,-1)

labels_n = np.zeros(length)

udp_packet = 0
tcp_packet = 0
dns_packet = 0
other = 0
total_packet = 0
n_a = 0
n_q = 0
    
printb = 0
i=0
for ts, buf in normal:
#     eth = dpkt.ethernet.Ethernet(buf)
    eth = dpkt.ethernet.Ethernet(buf)
        
    total_packet += 1 

    ip = eth.data
    ips_n[i] = int.from_bytes(ip.src,"little")
    protocol_n[i] = ip.p
    total_length_n[i] = ip.len

    if ip.p == 17:
        udp_packet += 1
        udp = ip.data
        
        dns = dpkt.dns.DNS(udp.data)
        dns_packet += 1

#                 dns = scapy.layers.dns.DNS(UDP.data)

        dns_opcode_n[i] =  dns.opcode
        dns_answerlength_n[i] = len(dns.an)
        dns_questionlength_n[i] = len(dns.qd)

        dns_flag_response_n[i] = dns.qr
        dns_flag_truncated_n[i] = dns.tc
        dns_flag_authorative_n[i] = dns.aa #authorative answer
        dns_flag_recursiond_n[i] = dns.rd
        dns_flag_recursiona_n[i] = dns.ra
        dns_reply_code_n[i] = dns.rcode

        if (dns.an):
            dns_answer_type_n[i] = dns.an[0].type
            try:
                dns_answer_name_n[i] = int.from_bytes(bytes(dns.an[0].name[:8],'utf-8'), "little")
            except:
                print(dns.an[0].name)
            dns_answer_class_n[i] = dns.an[0].cls
            dns_answerlength_n[i] = dns.an[0].rlen
        else:
            n_a +=1
        if (dns.qd):
            dns_question_class_n[i] = dns.qd[0].cls
            dns_question_name_n[i] = int.from_bytes(bytes(dns.qd[0].name[:8],'utf-8'), "little")
            dns_question_type_n[i] = dns.qd[0].type
        else:
            n_q +=1

        dst_port_n[i] = udp.dport
        src_port_n[i] = udp.sport
        udp_length_n[i] = udp.ulen

    i += 1

input.close()
print("total # of packets: %s"  % (total_packet))
print("# of UDP packets: %s" % (udp_packet))
print("# of TCP packets: %s" % (tcp_packet))
print("# of DNS packets: %s" % (dns_packet))
print("# of other packets except for TCP or UDP: %s"  % (other))
print("# no answer: %s" % (n_a))
print("# no question: %s" % (n_q))
end = time.time()
print(end - start)


total # of packets: 4372
# of UDP packets: 4372
# of TCP packets: 0
# of DNS packets: 4372
# of other packets except for TCP or UDP: 0
# no answer: 2587
# no question: 0
0.21501922607421875


In [49]:
input = open('attack_pcaps/07618097a64126cfe87e099b3054a073.pcap', 'rb')
# input = open('attack_pcaps/41fd4b0156a33263722ee03c74e238a4.pcap', 'rb')
normal = dpkt.pcap.Reader(input)
check = 0
counter = 0

# pcap = 'attack_pcaps/41fd4b0156a33263722ee03c74e238a4.pcap'
# pkts = rdpcap(pcap)

# print(type(pkts[0]))
print("start")
for ts, buf in normal:

    pkt = scapy.layers.l2.Ether(buf + b'\x01\x01\x00\x02')
    
#     dns = pkt['DNS']
    check += 1
    print("#", check)
    if pkt.haslayer(IP):
        ip = pkt['IP']
        if ip.proto == 6:
            tcp = pkt['TCP']
        elif ip.proto == 17:
            udp = pkt['UDP']
#             payload = 'ZZZZZZZZZZZZZZZZZZZZZ'
#             pkt = pkt / payload
            print(pkt['Raw'])
#             if not pkt.haslayer(DNS):
# #                 dns = scapy.layers.dns.DNS(buf + b'\x01\x01\x00\x02\x01\x01\x00\x02')#, '\x01\x01\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x04\x00\x00\x00')#\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')#\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')# + b'\x01\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')#\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')
#                 print(dns.rd.)
            
#     ip = pkt['IP']
#     udp = pkt['UDP']
#     dns = pkt['DNS']
        
#         print("#", check)
# #         dd = UDP.data
#         print(UDP.ulen)
# #         if(UDP.ulen > 1800):
# #             continue
#         try:
#             if buf.haslayer(DNS):
#                 dns = scapy.layers.dns.DNS(dd)
#         except:
#             dns = scapy.layers.dns.DNS(dd)
            
print(counter)

start
# 1
b'm\x0c\x81\x80\x00\x01\x00\x1d\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x06\x00\x01\x00\x00\x1a\x0e\x00:\x03ns1\xc0\x0c\x1dit.aciouns.external.dns.admin\xc0\x0cw\xcfu\x0e\x00\x00*0\x00\x00\x0e\x10\x00$\xea\x00\x00\x00\x03\x84\xc0\x0c\x00.\x00\x01\x00\x00\x1a\x0e\x00\x9b\x00\x06\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x03irs\x03gov\x00\x80\x9d\x9b\xce\xbe~\x93\xc5eL\x8b\xc6\x99\xf72U?\x92Y\xf2!O\x1d\x95^\xdf\xa5\xea2\x1boK,\x1c`,\xa3-\xe3\xe4\x03$\x05s0e\xceQ\xc2\xdc0|\x92\xa7\xb3\x19nn\xcef\xb21\x90u"\x80Gj\xfb\x08\x08\xa4=Ge\xc7"\n\xd0\xcb\xb3\xe2\xb2\x1f_\xe6\x18\x15\xa0\x1c!\xd5]ri\x01\x0fw\x8f.\xd31\xd2r\x9c\xfd\xe3\xf4W\x12\x9e\x81\xa6;{\xa2\xae"k\x86(\xea\xc16\xbb\xfb\xa5\x11\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg4\xc0\x0c\xc

# 92
b't\x87\x81\x80\x00\x01\x00\x1d\x00\x00\x00\x07\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg5\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg6\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\x14\x04emgw\xc0\x0c\xc0\x0c\x00.\x00\x01\x00\x00\x1bx\x00\x9b\x00\x0f\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x03irs\x03gov\x00\x9e\x11B\xc0\xe4\xb5np9O\x155f\xaf\x99{\xbf\xb6$\xd1\x9b\x14\xd8\n\xf0\xd7\xc0\x0f\xe3\xe7]Z\xaab\x99y\x08\x02\xcc,\xdb\xb9-\x7f,\xdc\x17\xb5\xf1\x9e\x0bA\x0c\x05w\xe4\xb1\xea\x80E\x95(5\xc0T\xb0\xbe\x7f\xbe\x18I\xf7qe0\xd4 \xe3dt\x82hY\x83\xd5\x9d\xc3V\x9c\x94\xfc\xd7\xb1C\xe2\xb8\xe4\xa3\xd3\x1ck\xda\xde\xbe\xa6\x06\xafG\x15\x87\xb3\x82\xaf\

# 211
b'ko\x81\x80\x00\x01\x00\x1d\x00\x00\x00\x07\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg5\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg6\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\x14\x04emgw\xc0\x0c\xc0\x0c\x00.\x00\x01\x00\x00\x18[\x00\x9b\x00\x0f\x07\x02\x00\x00\x1c T\xa3f\xdeT\x9a\x1eNt!\x03irs\x03gov\x00w\xa0\xac?\x03+\x98\xe3\x19g\x90\xab\xfd\xc0\xf0{\xb1f\xbdp\xf7T6\xd9Lz\xce\xce\xed<\xcd\x91^<\x12A\xf0\xebaS/\x00\xe2\xca\xcd\xba\x92\x98\x93\x84\x02\x83\xbeY.\x881\x1d0\xbf%\xc9\xb9\xd7OE\xb5\xbd\xa9\x988L\xd4\xbb\x1a\xce\x0b\x1b\xd0g\x032$\r\\\tG\xa2\xf8\x05\x08m\xe4"\xf2\xe5\xe8\x88=\x13G\x85RG\xb61\xa0\xde+#\xa3KR\xde\xb0\xb3\xb3\xe9\xa8qDr\

# 264
b't\x87\x81\x80\x00\x01\x00\x1d\x00\x00\x00\r\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x01\x00\x01\x00\x00\x01\xc9\x00\x04\xa6{\xda\xdc\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns1\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns2\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns3\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns4\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns5\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns6\xc0\x0c\xc0\x0c\x00\x06\x00\x01\x00\x00\x1b\x91\x006\xc05\x1dit.aciouns.external.dns.admin\xc0\x0cw\xcfu\r\x00\x00*0\x00\x00\x0e\x10\x00$\xea\x00\x00\x00\x03\x84\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00

# 335
b'ko\x81\x80\x00\x01\x00\x19\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x003\x00\x01\x00\x00\x15\xdb\x00\t\x01\x00\x00d\x04\xaa\xbb\xcc\xdd\xc0\x0c\x00.\x00\x01\x00\x00\x15\xdb\x00\x9b\x003\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x03irs\x03gov\x00\x1f\xf8Xk}C/\xc0\x05r\xf8\xb3\x80\x98<\xc9\x8at\xae<w\x08\xefU(U\xbc\x00\xcf\x07y\xdf\xcc\xe8m\x07\xf3\xaa\x03e\xb0\x08\x89C\x1e&\xd0\xaa\x03Q\xee\x17\x86\x0bi\\1a\xb4\xca\xfe_\xc2\xf559\xf0\x10\xf9\xf6\x00\xb27D\x19\x80\xceg\xda\x02\xdb\xddz\xf9\x1e\xb1\xb2f20\xab\x921]\xf0:\xe6\xcc\x91\xfa\xd7hPR\x8d\xcb\xc2]^x\xedK\xc7wx\x88\xb7N(E\xe5)[\xb3o\xf4\xfaT\xc0\x0c\x000\x00\x01\x00\x00\x15\xdb\x00\x88\x01\x00\x03\x07\x03\x01\x00\x01\xb2\xc2\xba\xe3\xde\x86\x06\xcaR\\\x12%\xa2\x1f\xd7\x98\r\xc5\x16\xdd\t6\xfe\x9b\xf5:g\xd2j\x1c\x05\xadB\x06\x9e\xf1w\x839\x9dN\x1d\x83\xdc0\x04)\x90\x8ak\x84v\xda}\xf8\xa1@\x08\xd0?\xdcj\xb1\x892\x17\x00\xac\xcb\x05wd\xb9)\xc5\x95=\r\xddI\xb4\xa0\x96w\xf0\xb0\xe6Pt\x0c\xf1}^\xcc\x9d\xb1fvw\xf

...

# 726
b't\x87\x81\x80\x00\x01\x00\x1d\x00\x00\x00\r\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x01\x00\x01\x00\x00\x01\xc8\x00\x04\xa6{\xda\xdc\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns1\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns2\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns3\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns4\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns5\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns6\xc0\x0c\xc0\x0c\x00\x06\x00\x01\x00\x00\x1b\x90\x006\xc05\x1dit.aciouns.external.dns.admin\xc0\x0cw\xcfu\r\x00\x00*0\x00\x00\x0e\x10\x00$\xea\x00\x00\x00\x03\x84\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00

# 795
b't\x87\x81\x80\x00\x01\x00\x19\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00.\x00\x01\x00\x00\x15\xdb\x01\x1b\x000\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcd\x03v\x03irs\x03gov\x00THm\x19\xd7wUG\xcc4\xbb\x96\x90\xb0\x19\x80\xec\xf3J\xd5\x81M\xad\xb6vs\x077\x0e\x97d\xf8<#\xe9\xdb\xc3\x02\x14\xba\xeb\x94\xef\xfc\x14"7\xa1\xf4Q\npj\x88\xaa\xd0\xab\x01\xa8F\x1f\xe8\xe6\xd6\xa7,\xaeY\xe5en\xc3\x87U\xc1/\x9e`G\xf1j\xdfm\xc43[\xdeg\x16\x1d\xfb\xbdW\xaeF\x01\xed\xdeFh[c*\x13\x90\'\x94\xc4AP\xfdS\xa6`\xfe\xfejkB\xe7\xfc\xa40\xd0\xc3<\xcbscevM\xbd\xea\xb8\x94\xdc\x9at\xe1\ts3\xb0\xbcc\xfd*\x15\xbc\xa5D\xb2\xf7\xbc9\x88\xaf\x14YN\x9c;\x1b\x86tfj\x88\x8a\x15\\\xfb\xadUI\x859\xa1!\xfb&\xae7\xe1\xfd\xc9\x1e\x0f\'\xd0(x\xda\xfaj\x16\xb8onhQ\x03\x93\xed\x8co\x94g\xdc\xafPeQ\x9e\xa5.\x86\xc1\xdc\rbT\xb9B=\xdc\xb8RH\xc5\x0cJ\xfe\xde\xd5<E\xec\x98\xb2/I\x9c\xdc\xecFk\xc8>\xfed\xab\x06\xbdM\xc0\x0c\x00.\x00\x01\x00\x00\x15\xdb\x00\x9b\x000\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x0

b'\x1e\xd5\x81\x80\x00\x01\x00\x1f\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x0f\x00\x01\x00\x00\x08C\x00\t\x00\x14\x04emgw\xc0\x0c\xc0\x0c\x00.\x00\x01\x00\x00\x07+\x00\x9b\x00\x0f\x07\x02\x00\x00\x1c T\xa3f\xdeT\x9a\x1eNt!\x03irs\x03gov\x00w\xa0\xac?\x03+\x98\xe3\x19g\x90\xab\xfd\xc0\xf0{\xb1f\xbdp\xf7T6\xd9Lz\xce\xce\xed<\xcd\x91^<\x12A\xf0\xebaS/\x00\xe2\xca\xcd\xba\x92\x98\x93\x84\x02\x83\xbeY.\x881\x1d0\xbf%\xc9\xb9\xd7OE\xb5\xbd\xa9\x988L\xd4\xbb\x1a\xce\x0b\x1b\xd0g\x032$\r\\\tG\xa2\xf8\x05\x08m\xe4"\xf2\xe5\xe8\x88=\x13G\x85RG\xb61\xa0\xde+#\xa3KR\xde\xb0\xb3\xb3\xe9\xa8qDr\xb6\xd3\x0bK\x0c\xa0\xc0\x0c\x00.\x00\x01\x00\x00\x07+\x00\x9b\x00\x02\x07\x02\x00\x00\x1c T\xa3f\xdeT\x9a\x1eNt!\x03irs\x03gov\x00_\xf9\x04\x1c\xee\xd0\xa3J^`\xdcj_\xa4\x86M|\xb2n\x82\xf6]\x10\x83\x15\xef;\xfe\xe5\x9e\xebw\xaa\xf3\x01\x9d\x18\\\xe4\xb8z\xe6\xb4!\xd9\x01\xfd\xfbl\xf3\xe3Q\x88\xf3\x1e\xaf\x02\x13\xa5K\x02\x98\x03\x8d\x94\xfdde]f\x0c\xaf\x13\x9a\xd6\xd1\x8cH\\Wy!\x1d\x0c\x

# 968
b'n\x12\x81\x80\x00\x01\x00\x1b\x00\x06\x00\x14\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00.\x00\x01\x00\x00\x0bo\x00\x97\x00+\x08\x02\x00\x00\x0e\x10T\xa5\x1d\x06T\x9b\xe2\x863\x9e\x03gov\x00*\x97\x1b\x92\x8e\xfcC\x06\xcf\x02\xb6 %t\xeb\xf2;X`\x0e\x8b\x07\x0fa\xc3\x0ea?\xd2o\xe4\x90&\x811\xe9\x86n\x06m\x08\x8e\xc4\xd4\xbf?\x0fS\xa0\xbd\x8bS\xa3\xc4\x94\xef\xa1\xc5\xd0[5p\xd37\x93\xbb)\x9f\x8a\x0b\x03r\xeb!c:\xf1G:\xd18\xe7\xd3\xddD\xe4\x04\'\x1e$\x91]\xf6\x81\xaaRYG\xcbc\xd3\x16\xab\x94\xc4\x07C\x8e\x8f\x8d\x04\xf6\x1ek\x17)\xe7\x80~T%\xd9\x0f^V@\xe6\x16\xc0\x0c\x00+\x00\x01\x00\x00\x0bo\x00$\x03v\x07\x02\x83\x9f\x8b\xf5\xd6\x00\xecOm.\xa7\x8c\x8e\xaf\xaf<\x9a\x00\xf9\x06\xdb\nG\x1f\x18u.\xd6+\x93\x08\xae\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns1\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns3\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns4\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns6\xc0\x0c\xc0\x0c\x00\x02\x00\x01\

KeyboardInterrupt: 

### Get attack keys of DDoS attacks containing only DNS traffic

In [4]:
path_to_json = 'signatures/'
json_files = [pos_json for pos_json in os.listdir(path_to_json) if pos_json.endswith('.json')]

dns_keys=[]

for jf in json_files:
    with open('signatures/' + jf) as f:
        data=json.load(f)
    protocol = data.get("protocol")

    if protocol == "DNS":
        dns_keys.append(jf[:-5])

print("# of DNS DDoS attacks: ", len(dns_keys))

# of DNS DDoS attacks:  45


### Get AMI score and other stats per DNS DDoS Attack

In [5]:
start = time.time()
most_important_features = []
AMI_values = {}
counter = 0
#iterate over all attack keys with DNS attacks
with open('dns_attacks.csv', 'r') as f:
    reader = csv.reader(f)
    dns_keys = list(reader)

for attack_key in dns_keys:
    try:
        input = open('attack_pcaps/' + attack_key[0] + '.pcap', 'rb')
        attack = dpkt.pcap.Reader(input)
        
        udp_packet = 0
        tcp_packet = 0
        dns_packet = 0
        other = 0
        total_packet = 0
        n_a = 0
        n_q = 0
        
        c = False
        ############### 
        #loop trough packets to get the number of packets in the attack
        #############
        for ts, buf in attack:
            eth = dpkt.ethernet.Ethernet(buf)
            total_packet += 1 
            if total_packet > 100000:
                print("continue")
                print("##########")
                c = True
                break
                
#         if c:
#             continue
            
        input.close()
        counter += 1
        print("# ", counter, "/", len(dns_keys))
        print("attackkey: ", attack_key[0])
        print("total # of packets: %s"  % (total_packet))

        #######################*dns*
        #initialize numpy arrays for all the to measure features
        ##############################
        
        ips_a = np.full(total_packet, -1)
        protocol_a = np.full(total_packet, -1)
        total_length_a = np.full(total_packet, -1)
        src_port_a = np.full(total_packet, -1)
        dst_port_a = np.full(total_packet, -1)
        udp_length_a = np.full(total_packet, -1)
        
        dns_opcode_a = np.full(total_packet, -1)
        dns_answerlength_a = np.full(total_packet, -1)
        dns_questionlength_a = np.full(total_packet, -1)
        dns_additional_recordlength_a = np.full(total_packet, -1)
        dns_RRlength_a = np.full(total_packet, -1)

        dns_flag_response_a = np.full(total_packet, -1)
        dns_flag_truncated_a = np.full(total_packet, -1)
        dns_flag_authorative_a = np.full(total_packet, -1)
        dns_flag_recursiond_a = np.full(total_packet, -1)
        dns_flag_recursiona_a = np.full(total_packet, -1)

        dns_reply_code_a = np.full(total_packet, -1)

        dns_answer_type_a = np.full(total_packet, -1)
        dns_answer_class_a = np.full(total_packet, -1)
        dns_answer_name_a = np.full(total_packet, -1)
        dns_answer_size_a = np.full(total_packet, -1)

        dns_question_name_a = np.full(total_packet, -1)
        dns_question_class_a = np.full(total_packet, -1)
        dns_question_type_a = np.full(total_packet, -1)
        
        labels_a = np.ones(total_packet)    
        
        ###############
        #loop trough packets and gather features
        #########
        input = open('attack_pcaps/' + attack_key[0] + '.pcap', 'rb')
        attack = dpkt.pcap.Reader(input)
        i = 0
        
        for ts, buf in attack:
            if i == (total_packet -1):
                break
            eth = dpkt.ethernet.Ethernet(buf)

            ip = eth.data
            ips_a[i] = int.from_bytes(ip.src,"little")
            protocol_a[i] = ip.p
            total_length_a[i] = ip.len
            if ip.p == 6:
                tcp_packet += 1
                tcp = ip.data
                dst_port_a[i] = tcp.dport
                src_port_a[i] = tcp.sport
            elif ip.p == 17:
                udp_packet += 1
                udp = ip.data
                if udp.sport == 53 or udp.dport==53:
                    dns_packet += 1
                    dns = dpkt.dns.DNS(udp.data)
                    #dns = scapy.layers.dns.DNS(UDP.data)

                    dns_opcode_a[i] =  dns.opcode
                    dns_answerlength_a[i] = len(dns.an)
                    dns_questionlength_a[i] = len(dns.qd)

                    dns_flag_response_a[i] = dns.qr
                    dns_flag_truncated_a[i] = dns.tc
                    dns_flag_authorative_a[i] = dns.aa #authorative answer
                    dns_flag_recursiond_a[i] = dns.rd
                    dns_flag_recursiona_a[i] = dns.ra
                    dns_reply_code_a[i] = dns.rcode

                    if (dns.an):
                        dns_answer_type_a[i] = dns.an[0].type
                        dns_answer_name_a[i] = int.from_bytes(bytes(dns.an[0].name[:8],'utf-8'), "little")
                        dns_answer_class_a[i] = dns.an[0].cls
                        dns_answerlength_a[i] = dns.an[0].rlen
                    else:
                        n_a +=1
                        
                    if (dns.qd):
                        dns_question_class_a[i] = dns.qd[0].cls
                        dns_question_name_a[i] = int.from_bytes(bytes(dns.qd[0].name[:8],'utf-8'), "little")
                        dns_question_type_a[i] = dns.qd[0].type
                    else:
                        n_q +=1

                    dst_port_a[i] = udp.dport
                    src_port_a[i] = udp.sport
                    udp_length_a[i] = udp.ulen
            else:
                other += 1
                dst_port_a[i] = 0
                src_port_a[i] = 0


            i += 1
        
        ###############
        #make Numpy arrays with attack features and normal features together
        ################
        ips = np.append(ips_a, ips_n)
        protocol = np.append(protocol_a, protocol_n)
        total_length = np.append(total_length_a, total_length_n)
        src_port = np.append(src_port_a, src_port_n)
        dst_port = np.append(dst_port_a, dst_port_n)
        udp_length = np.append(udp_length_a, udp_length_n)
        
        dns_opcode = np.append(dns_opcode_a, dns_opcode_n)
        dns_answerlength = np.append(dns_answerlength_a, dns_answerlength_n)
        dns_questionlength = np.append(dns_questionlength_a, dns_questionlength_n)
#         dns_RRlength = np.append(dns_RRlength_a, dns_RRlength_n)
#         dns_additional_recordlength = np.append(dns_additional_recordlength_a, dns_additional_recordlength_n)
        
        dns_flag_response = np.append(dns_flag_response_a, dns_flag_response_n)
        dns_flag_truncated = np.append(dns_flag_truncated_a, dns_flag_truncated_n)
        dns_flag_authorative = np.append(dns_flag_authorative_a, dns_flag_authorative_n)
        dns_flag_recursiond = np.append(dns_flag_recursiond_a, dns_flag_recursiond_n)
        dns_flag_recursiona = np.append(dns_flag_recursiona_a, dns_flag_recursiona_n)

        dns_reply_code = np.append(dns_reply_code_a, dns_reply_code_n)

        dns_answer_type = np.append(dns_answer_type_a, dns_answer_type_n)
        dns_answer_class = np.append(dns_answer_class_a, dns_answer_class_n)
        dns_answer_name = np.append(dns_answer_name_a, dns_answer_name_n)
        dns_answer_size = np.append(dns_answer_size_a, dns_answer_size_n)

        dns_question_name = np.append(dns_question_name_a, dns_question_name_n)
        dns_question_class = np.append(dns_question_class_a, dns_question_class_n)
        dns_question_type = np.append(dns_question_type_a, dns_question_type_n)
        
        labels = np.append(labels_a, labels_n)

        features = [ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type]

        
        ##########
        #Calculate adjusted mutual information score
        ############
        
        scores = []
        for x in features:
            score = adjusted_mutual_info_score(np.repeat(x,4), np.repeat(labels,4), "arithmetic")
            scores.append(score)
        AMI_values[attack_key[0]] = scores
        ###########
        #Print all stats per attack
        #######

        print("# of UDP packets: %s" % (udp_packet))
        print("# of TCP packets: %s" % (tcp_packet))
        print("# of DNS packets: %s" % (dns_packet))
        print("# of other packets except for TCP or UDP: %s"  % (other))
        print("Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type")
        print("AMI scores: ", scores)
        
#         fname = "signatures/" + attack_key[0] + ".json"
#         with open(fname) as jsonfile:
#             sig = json.load(jsonfile)
#         sig['AMI_DNS'] = scores
#         with open(fname, mode='w') as f:
#             f.write(json.dumps(sig, indent=2))
        
        
        max_index, max_value = max(enumerate(scores), key=operator.itemgetter(1))
        most_important_features.append(max_index)
        print("Most important feature: ", max_index)
        end = time.time()
        print(end - start)
        print("#####################################")
    except Exception as e:
        print("something went wrong here ", attack_key[0])
        exc_type, exc_obj, exc_tb = sys.exc_info()
        fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
        print(exc_type, fname, exc_tb.tb_lineno)
        print(e)
print(end - start)

#  1 / 45
attackkey:  01dd938e512bd560020dee459a32a5d5
total # of packets: 20004
# of UDP packets: 20003
# of TCP packets: 0
# of DNS packets: 20003
# of other packets except for TCP or UDP: 0
Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type
AMI scores:  [0.24606923020385174, 8.881086322074704e-06, 0.24952305388289497, 0.2402704684161861, 0.07042382094762531, 0.24952305388289497, 8.881086322074704e-06, 0.3340364668229479, 8.881086322074704e-06, 0.4660161574067123, 8.881086322074704e-06, 0.004726918896776001, 8.881086322074704e-06, 0.4660161574067123, 0.09424753584429238, 0.37646289240446523, 0.5358149908645055, 0.6033057115276032, -4.1251515854758016e-15, 0.4551454687805918, 8.881086322074704e-0

# of UDP packets: 12890
# of TCP packets: 0
# of DNS packets: 12890
# of other packets except for TCP or UDP: 0
Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type
AMI scores:  [0.30577664051961573, 2.8508435254205804e-05, 0.30709216168163567, 0.20829751966841606, 0.5035954975096126, 0.30709216168163567, 2.8508435254205804e-05, 0.42583743678396063, 2.8508435254205804e-05, 0.4384009517642018, 2.8508435254205804e-05, 0.004442878029901473, 2.8508435254205804e-05, 0.4384009517642018, 0.087379365288336, 0.4835993003897235, 0.5072458935114452, 0.563656087676226, -4.749515998634743e-15, 0.4152802708417576, 2.8508435254205804e-05, 0.8982461350903879]
Most important feature:  21
39.52068305015564
##########

#  17 / 45
attackkey:  45efbd82e475f6ec51928fbeb00aab86
total # of packets: 38935
# of UDP packets: 38934
# of TCP packets: 0
# of DNS packets: 38934
# of other packets except for TCP or UDP: 0
Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type
AMI scores:  [0.16224954786330678, -2.7358270644822663e-06, 0.23313983068878585, 0.28461643686573046, 0.04127736826153866, 0.23313983068878585, -2.7358270644822663e-06, 0.2350260282099569, -2.7358270644822663e-06, 0.49957086536645035, 0.018137340335426147, 0.005106240856486358, -2.7358270644822663e-06, 0.49957086536645035, 0.10303434773983124, 0.25064657087805603, 0.5095823505274056, 0.618397398055707, 0.0, 0.5086164244911516, -2.7358270644822663e-06, 0.927

#  25 / 45
attackkey:  7ae2d3d7a61ffe32d239cc2e68335bbb
total # of packets: 23009
# of UDP packets: 23008
# of TCP packets: 0
# of DNS packets: 23008
# of other packets except for TCP or UDP: 0
Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type
AMI scores:  [0.24338958308714895, 5.073980320407458e-06, 0.2748873062240524, 0.2500391753546488, 0.06328085173800789, 0.2748873062240524, 5.073980320407458e-06, 0.31894422703384817, 5.073980320407458e-06, 0.4738451696157251, 0.005394343054777581, 0.004812240194827603, 5.073980320407458e-06, 0.4706835482826211, 0.09080173982104023, 0.39026847689167166, 0.5384758454084716, 0.6118817309024656, 3.847760034440384e-15, 0.4670747418792789, 5.073980320407458e-06, 

# of UDP packets: 13757
# of TCP packets: 0
# of DNS packets: 13757
# of other packets except for TCP or UDP: 0
Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type
AMI scores:  [0.3006995480914871, 2.4696251961236447e-05, 0.21846613609272925, 0.21314347666434652, 0.50998019426629, 0.21846613609272925, 2.4696251961236447e-05, 0.22847536672495228, 2.4696251961236447e-05, 0.44279548988277717, 0.5054239028653467, 0.004486260879210936, 2.4696251961236447e-05, 0.44279548988277717, 0.08844994050437457, 0.2860764273844438, 0.20735491661706645, 0.3957025294779972, -1.468507892278672e-14, 0.4214131601906999, 2.4696251961236447e-05, 0.9004951599769409]
Most important feature:  21
153.17926025390625
##########

#  41 / 45
attackkey:  d99f6d570c052b54911cd2cc894cbbe3
total # of packets: 47140
# of UDP packets: 47139
# of TCP packets: 0
# of DNS packets: 47139
# of other packets except for TCP or UDP: 0
Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type
AMI scores:  [0.14784783681827834, -3.894755687813084e-06, 0.19160011575980587, 0.2962870990500555, 0.03504014481613899, 0.19160011575980587, -3.894755687813084e-06, 0.16233050842325425, -3.894755687813084e-06, 0.5076292857069052, 0.02165165230830617, 0.005202230418722793, -3.894755687813084e-06, 0.27145707919759543, 0.006806816494550851, 0.1820065974107325, 0.25560792787518033, 0.4535262690872457, 3.4706936666447635e-14, 0.5224694555005599, -3.894755687813

In [ ]:
with open('data.json', 'w') as json_file:
  json.dump(AMI_values, json_file)


### Analysis and Conclusions

In [ ]:
for i in range(0,22):
    print(i,most_important_features.count(i))

0 ips, <br/>
1 protocol, <br/>
2 total_length, <br/>
3 src_port, <br/>
4 dst_port, <br/>
5 udp_length, <br/>
6 dns_opcode, <br/>
7 dns_answerlength, <br/>
8 dns_questionlength, <br/>
9 dns_flag_response, <br/>
10 dns_flag_truncated, <br/>
11 dns_flag_authorative, <br/>
12 dns_flag_recursiond, <br/>
13 dns_flag_recursiona, <br/>
14 dns_reply_code, <br/>
15 dns_answer_type, <br/>
16 dns_answer_class, <br/>
17 dns_answer_name, <br/>
18 dns_answer_size, <br/>
19 dns_question_name, <br/>
20 dns_question_class, <br/>
21 dns_question_type <br/>